In [39]:

import pandas as pd
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly.offline.offline import _plot_html
import numpy as np
import cufflinks as cf
import os
import datetime
from datetime import timedelta
from bokeh.models import HoverTool, ColumnDataSource, BoxZoomTool
from bokeh.models.layouts import Column
from bokeh.layouts import gridplot
from bokeh.plotting import figure, show, output_file
from bokeh.io import output_notebook,vplot
pd.set_option("display.max_rows",1000)
init_notebook_mode()

In [40]:
# obter simbolos e filenames do json
symbol_list = ['EUR/AUD']

s = symbol_list[0].replace("/", "")  ##remove '/' from the string
filename = s + '_m1_2015'
s_file = s + '_report'

reportf = pd.read_json(os.path.join('/home/user/Desktop/algotrader/' + '% s.json' % 'reportf'), typ='series')
print reportf

df = pd.io.parsers.read_csv(
                os.path.join('/home/user/Desktop/algotrader/sandbox/' + filename), usecols=['Close', 'Day', 'Time'],
                                    parse_dates=True,
                                    names=['Type', 'Day', 'Time', 'Open', 'Max', 'Min', 'Close']
                                    )


df2 =  pd.io.parsers.read_csv(os.path.join('/home/user/Desktop/algotrader/', '% s.csv' % s_file),
                                    parse_dates=True,
                                    names=['Buy','Buy_Y', 'Sell','Sell_Y', 'Close', 'Close_Y']
                                    )

equity =  pd.io.parsers.read_csv(os.path.join('/home/user/Desktop/algotrader/', '% s.csv' % 'equity'),
                                    parse_dates=True, header=0,
                                    names=['Datetime','Position', 'Cash','Comission', 'Total', 'Returns', 'Equity_Curve', 'Drawdown']
                                    )
   
# set collumns to datetime
equity['Datetime'] = pd.to_datetime(equity['Datetime'])
equity = equity.set_index(equity['Datetime'])
df2['Buy'] = pd.to_datetime(df2['Buy'])
df2['Sell'] = pd.to_datetime(df2['Sell'])
df2['Close'] = pd.to_datetime(df2['Close'])

df['SMA20'] = pd.rolling_mean(df['Close'], 20)
df['SMA50'] = pd.rolling_mean(df['Close'], 50)
df['SMA100'] = pd.rolling_mean(df['Close'], 100)
df['SMA200'] = pd.rolling_mean(df['Close'], 200)



consecutive_losses                 4
consecutive_wins                  21
drawdown_duration               3509
filename              EURAUD_m1_2015
instruments                [EUR/AUD]
len_bars                       30461
len_buy                          475
len_sell                         467
loss_buy                     -559.56
loss_sell                    -601.76
max_drawdown                 0.8984%
profit                       4.1036%
profit_buy                    800.16
profit_sell                   771.52
sharpe                       5.22612
volatility                      None
dtype: object


/home/user/anaconda3/envs/py27/lib/python2.7/site-packages/ipykernel/__main__.py:35: FutureWarning:

pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=20,center=False).mean()

/home/user/anaconda3/envs/py27/lib/python2.7/site-packages/ipykernel/__main__.py:36: FutureWarning:

pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=50,center=False).mean()

/home/user/anaconda3/envs/py27/lib/python2.7/site-packages/ipykernel/__main__.py:37: FutureWarning:

pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=100,center=False).mean()

/home/user/anaconda3/envs/py27/lib/python2.7/site-packages/ipykernel/__main__.py:38: FutureWarning:

pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=200,center=False).mean()



In [41]:
date_index = []

for ir in df.itertuples():
    date = str(ir[1]) + ' ' + str(ir[2])
    # print date
    date = datetime.datetime.strptime(date, "%Y.%m.%d %H:%M")
    date_index.append(date)
    previousdata20 = date + timedelta(minutes=-20)
    previousdata50 = date + timedelta(minutes=-50)
    previousdata100 = date + timedelta(minutes=-100)
    previousdata200 = date + timedelta(minutes=-200)
    if date.weekday() == 6:
        if previousdata20.weekday() != 6:
            ir[4] = None
        if previousdata50.weekday() != 6:
            ir[5] = None
        if previousdata100.weekday() != 6:
            ir[6] = None
        if previousdata200.weekday() != 6:
            ir[7] = None    

df = df.set_index([date_index])
df.head()



Day   Time    Close  SMA20  SMA50  SMA100  SMA200
2015-01-01 13:16:00  2015.01.01  13:16  1.48140    NaN    NaN     NaN     NaN
2015-01-01 13:17:00  2015.01.01  13:17  1.48041    NaN    NaN     NaN     NaN
2015-01-01 13:18:00  2015.01.01  13:18  1.48013    NaN    NaN     NaN     NaN
2015-01-01 13:19:00  2015.01.01  13:19  1.48013    NaN    NaN     NaN     NaN
2015-01-01 13:20:00  2015.01.01  13:20  1.48011    NaN    NaN     NaN     NaN

In [42]:
output_notebook()
p1 = figure(x_axis_type="datetime")
p1.grid.grid_line_alpha=0.3
p1.xaxis.axis_label = 'Date'
p1.yaxis.axis_label = 'Price'

hover = HoverTool(
        tooltips=[
#             ("time", "$x{datetime}"),
            ("", "$y{1.1111}"),            
        ]
    )

# p = figure(plot_width=400, plot_height=400, tools=[hover],
#            title="Mouse over the dots
tools = [hover, 'reset', 'box_select','resize', 'pan','xzoom_out', 'yzoom_out', 'xwheel_zoom', 'ywheel_zoom','xbox_zoom', 'ybox_zoom']

p1 = figure(webgl=True, tools=tools, x_axis_type="datetime", title="Performance")
p1.line(df.index.values, df['Close'].values, color='#008000', legend=symbol_list[0])
# p1.circle('x', 'y1', color='white', legend=symbol_list[0], source=source)
p1.triangle(df2['Buy'].values, df2['Buy_Y'].values, color='blue', legend='OPEN-BUY orders', size=6)
p1.circle(df2['Sell'].values, df2['Sell_Y'].values, color='red', legend='OPEN-SELL orders', size=6)
p1.square(df2['Close'].values, df2['Close_Y'].values, color='black', legend='CLOSE orders', size=6)


# show(p1)


Loading BokehJS ...

GlyphRenderer(id='5029b30a-d9e0-411d-a2aa-84574a4865b4', ...)

In [43]:
 output_notebook()




source = ColumnDataSource(data=dict(x=df.index.values, y1=df['Close'].values, y2=equity['Returns'].values[:-1]))


tools = ['reset', 'resize', 'box_select', 'pan','zoom_out' ,'xwheel_zoom', 'ywheel_zoom','xbox_zoom', 'ybox_zoom']

hover = HoverTool(
        tooltips=("$y{1.1111}"))

# p = figure(plot_width=400, plot_height=400, tools=[hover],
#            title="Mouse over the dots
tools_hover = [hover, 'reset', 'box_select','resize', 'pan','zoom_out', 'xwheel_zoom', 'ywheel_zoom','xbox_zoom', 'ybox_zoom']
p1 = figure(webgl=True, tools=tools_hover, x_axis_type="datetime", title="Signals")
p1.toolbar.active_drag = None

# dates = df.index.apply(lambda x: dt.datetime.strptime(df.index.values,"%Y.%m.%d %H:%M"))
p1.line('x', 'y1', color='olive', legend=symbol_list[0], source=source)
p1.circle('x', 'y1', fill_color='white', size=6, legend=symbol_list[0], source=source)
p1.triangle(df2['Buy'].values, df2['Buy_Y'].values, color='red', legend='OPEN-BUY orders', size=7)
p1.inverted_triangle(df2['Sell'].values, df2['Sell_Y'].values, color='blue', legend='OPEN-SELL orders', size=7)
p1.square(df2['Close'].values, df2['Close_Y'].values, color='black', legend='CLOSE orders', size=7)
p1.line(df.index.values, df['SMA20'].values, color='orange', legend='SMA20')
p1.line(df.index.values, df['SMA50'].values, color='purple', legend='SMA50')
p1.line(df.index.values, df['SMA100'].values, color='brown', legend='SMA100')
p1.line(df.index.values, df['SMA200'].values, color='green', legend='SMA200')



p2 = figure(webgl=True, tools=tools, x_axis_type="datetime", title="Returns")
p2.segment('x', 0, 'x','y2', color="red", source=source, legend='Returns')
p2.circle('x', 'y2', fill_color="red", size=6, source=source, line_color='red', line_alpha=0)

# p3 = figure(webgl=True, tools=tools, x_axis_type="datetime")
# p3.line('x', 'y3', color="yellow", source=source, legend='Drawdown')
# p3.circle('x', 'y3', fill_color="yellow", size=6, source=source, line_color='yellow', line_alpha=0)

# p2 = figure()
# p2.circle('x', 'y2', color="olive", alpha=0.5, source=source)

# p = gridplot([[p1], [p2]])
# p = vplot(p1, p2)
p = Column(children=[p2,p1])
show(p)


Loading BokehJS ...

In [44]:
source = ColumnDataSource(data=dict(x=equity.index.values[1:], y1=equity['Equity_Curve'].values[1:], y2=equity['Drawdown'].values[1:]))


tools = ['reset', 'resize', 'box_select', 'pan','xzoom_out', 'yzoom_out', 'xwheel_zoom', 'ywheel_zoom','xbox_zoom', 'ybox_zoom']

p1 = figure(webgl=True, tools=tools, x_axis_type="datetime", title="Performance")
# dates = df.index.apply(lambda x: dt.datetime.strptime(df.index.values,"%Y.%m.%d %H:%M"))
p1.line('x', 'y1', color='blue', legend='Equity Curve', source=source)
p1.circle('x', 'y1', fill_color='blue', size=6, legend='Equity Curve', source=source)


p2 = figure(webgl=True, tools=tools, x_axis_type="datetime")
p2.segment('x', 0, 'x','y2', color="red", source=source, legend='Drawdown')
p2.circle('x', 'y2', fill_color="red", size=6, source=source, line_color='red', line_alpha=0)

# p2 = figure(webgl=True, tools=tools, x_axis_type="datetime")
# p2.line('x', 'y2', color="red", source=source, legend='Drawdown')
# p2.circle('x', 'y2', fill_color="red", size=6, source=source, line_color='red', line_alpha=0)

p = Column(children=[p1,p2])
show(p)
# factors = ["a", "b", "c", "d", "e", "f", "g", "h"]
# x =  [50, 40, 65, 10, 25, 37, 80, 60]

# dot = figure(title="Categorical Dot Plot", tools="", toolbar_location=None,
#             y_range=factors, x_range=[0,100])

# dot.segment(0, factors, x, factors, line_width=2, line_color="green", )
# dot.circle(x, factors, size=15, fill_color="orange", line_color="green", line_width=3, )

# 